# Dev 2

We've come along way with this project. Now we are thoroughly in the weeds. 

Our major goasls are to:
- make various updates to make it easier to scale with this project. Mainly storing artifacts (trajectories/models) on wandb. Once this is working, we can train on a lambda labs gpu on harder problems while having a complete record of events and results.
- next, I'd like to write more complicated analysis code to characterise various models. For starter, I'd like to get a calibration curve to evaluate DT's on their ability to "simulate" different qualities of agents. 

Side goals which I may do in parallel:
- abstract away from the DT to also have a BC model. 
- train the DT on predicting rewards, states and actions (this may improve sample efficiency and is fine from the perspective of the interpretability project). 



## Downloading artifacts from wandb

In [ ]:
import wandb
run = wandb.init()
artifact = run.use_artifact('arena-ldn/PPO-MiniGrid/MiniGrid-LavaGapS7-v0016df0e6-b5e6-40ed-a598-e75f228f45a8.pkl:v0', type='trajectory')
artifact_dir = artifact.download()

now I'll trigger the DT training script with this path.

It seems like the upload to wandb takes ages... possibly due to an unresolved issue. 

I will hold off on scaling up/using lambda while I try to improve on the DT, mainly by making it predict RTG and States as well.

# Investigate Trajectories

Things it would be good to control:
- train test split
- the reward per trajectory
- epochs
- batch size
- mask -> should we mask the padding tokens?

In [ ]:
# let's load some trajectories 
from src.decision_transformer.offline_dataset import TrajectoryLoader
from src.decision_transformer.decision_transformer import DecisionTransformer
from src.environments import make_env

trajectory_path = "trajectories/MiniGrid-DoorKey-8x8-v093a42bd3-2b15-4a7e-a0b9-4375ddf72e04.pkl"
# trajectory_path = "trajectories/MiniGrid-Dynamic-Obstacles-8x8-v0579f73fd-a62e-4239-a679-55fd341c23c7.pkl"
trajectory_data_set = TrajectoryLoader(trajectory_path, pct_traj=1, device="cpu")

env_id = trajectory_data_set.metadata['args']['env_id']
env = make_env(env_id, seed = 1, idx = 0, capture_video=False, run_name = "dev", fully_observed=False)
env = env()

# dt = DecisionTransformer(
#     env = env, 
#     d_model = 32,
#     n_heads = 2,
#     d_mlp = 64,
#     n_layers = 2,
#     state_embedding_type="grid", # hard-coded for now to minigrid.
#     max_timestep=trajectory_data_set.metadata.get("args").get("max_steps") # Our DT must have a context window large enough
# )



In [ ]:
state, action, reward, d, rtg, timesteps, mask = trajectory_data_set.get_batch(256, 100)


In [ ]:
from minigrid.core.constants import IDX_TO_OBJECT
import numpy as np
import torch

def find_agent(observation):
    height = observation.shape[0]
    width = observation.shape[1]
    for i in range(width):
        for j in range(height):
            object = IDX_TO_OBJECT[int(observation[i,j][0])]
            if object == 'agent':
                return i, j

    else:
        return -1,-1


def render_minigrid_observation(env, observation):
    if isinstance(observation, np.ndarray):
        observation = observation.copy() # so we don't edit the original object
    elif isinstance(observation, torch.Tensor):
        observation = observation.numpy().copy()

    agent_pos = find_agent(observation)
    agent_dir = observation[agent_pos[0], agent_pos[1]][2]

    observation[agent_pos[0], agent_pos[1]] = [0,0,0]

    grid, _ = env.grid.decode(observation.astype(np.uint8))
    
    i = agent_pos[0]
    j = agent_pos[1]
    
    return grid.render(32, (i,j), agent_dir=agent_dir)

def render_minigrid_observations(env, observations):
    return np.array([render_minigrid_observation(env, observation) for observation in observations])



frames = render_minigrid_observations(env, state[0][mask[0].to(bool)])
import moviepy.editor as    mpy
import numpy as np
 
 # write an mp4 file
clip = mpy.ImageSequenceClip(list(frames), fps=10)
clip.write_videofile("test.mp4", fps=10)


In [ ]:
import torch as t 
max([len(i) for i in trajectory_data_set.actions])

In [ ]:
# find the actions with length 1011

for i in range(len(trajectory_data_set.actions)):
    if len(trajectory_data_set.actions[i]) == 23:
        print(i)

frames = render_minigrid_observations(
    env, trajectory_data_set.states[272])
clip = mpy.ImageSequenceClip(list(frames), fps=10)
clip.write_videofile("test.mp4", fps=10)

In [ ]:
# video shows clearly that there is 1 successful trajectory and one failed trajectory in the dataset! 
# so we are missing a done? 

trajectory_data_set.rewards[6613][:20]

In [ ]:
trajectory_data_set.dones[6613][:20]

In [ ]:
# so the dones isn't there and the reward isn't there. 

# this is a mismatch between the actions and observations. 

# off by one?
trajectory_data_set.dones[6612][:20]


In [ ]:
trajectory_data_set.actions[6612][:20]

In [ ]:
# get len of each actions
import plotly.express as px 
px.histogram([len(i) for i in trajectory_data_set.actions])

In [ ]:
len(trajectory_data_set.actions)

In [ ]:
len(trajectory_data_set.states)

In [ ]:
(t.concat(trajectory_data_set.rewards) != 0).sum()

In [ ]:
trajectory_data_set.num_trajectories

In [ ]:
# so we have 271673 trajectories with non-zero rewards and 26173 trajectories


In [ ]:
26173 - 26442

In [ ]:
# 269 trajectories with rewards but no dones/truncations
# how? 

#trajectories that didn't get finished at the end of a minibatch? 
# in  this case we just have trajectory that is cut off half way.
# the agent is still alive, but the episode is over and it's not encoded. 
# how do we detect these? 
# They aren't 0 RTG trajectories since we don't know what the RTG is (it didn't finish)
# we need to remove them. 




In [ ]:
trajectory_data_set.dones[-1]

In [ ]:
trajectory_data_set.truncated[-1]

# Download a previous agent and calculate it's calibration



In [1]:
import wandb
run = wandb.init()
artifact = run.use_artifact('arena-ldn/DecisionTransformerInterpretability/MiniGrid-DoorKey-8x8-v0__Dev__1__1673268725:v0', type='model')
artifact_dir = artifact.download()

wandb: Currently logged in as: jbloomaus (arena-ldn). Use `wandb login --relogin` to force relogin


wandb:   1 of 1 files downloaded.  


In [1]:
# let's load some trajectories 
import torch as t 
from src.decision_transformer.offline_dataset import TrajectoryLoader
from src.decision_transformer.model import DecisionTransformer
from src.environments import make_env

trajectory_path = "trajectories/MiniGrid-DoorKey-8x8-v093a42bd3-2b15-4a7e-a0b9-4375ddf72e04.pkl"
trajectory_data_set = TrajectoryLoader(trajectory_path, pct_traj=1, device="cpu")

env_id = trajectory_data_set.metadata['args']['env_id']
env = make_env(env_id, seed = 1, idx = 0, capture_video=False, run_name = "dev", fully_observed=False, max_steps=30)
env = env()

dt = DecisionTransformer(
    env = env, 
    d_model = 128,
    n_heads = 4,
    d_mlp = 256,
    n_layers = 2,
    state_embedding_type="grid", # hard-coded for now to minigrid.
    max_timestep=1000) # Our DT must have a context window large enough

path = "artifacts/MiniGrid-DoorKey-8x8-v0__Dev__1__1673268725:v0/MiniGrid-DoorKey-8x8-v0__Dev__1__1673268725.pt"
dt.load_state_dict(t.load(path))

{'args': {'exp_name': 'MiniGrid-DoorKey-8x8-v0', 'seed': 1, 'cuda': True, 'track': True, 'wandb_project_name': 'PPO-MiniGrid', 'wandb_entity': None, 'capture_video': True, 'env_id': 'MiniGrid-DoorKey-8x8-v0', 'total_timesteps': 1000000, 'learning_rate': 0.00025, 'num_envs': 4, 'num_steps': 128, 'gamma': 0.99, 'gae_lambda': 0.95, 'num_minibatches': 4, 'update_epochs': 4, 'clip_coef': 0.2, 'ent_coef': 0.01, 'vf_coef': 0.5, 'max_grad_norm': 0.5, 'max_steps': 1000, 'trajectory_path': 'trajectories/MiniGrid-DoorKey-8x8-v093a42bd3-2b15-4a7e-a0b9-4375ddf72e04.pkl', 'fully_observed': False}, 'time': 1673261764.333065}


<All keys matched successfully>

In [2]:
from src.decision_transformer.train import evaluate_dt_agent
from src.environments import make_env

In [3]:
statistics = evaluate_dt_agent(
    env_id = env_id,
    dt = dt,
    make_env=make_env,
    track = False,
    batch_number = 0,
    initial_rtg=1,
    trajectories=50)

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/gymnasium/wrappers/record_video.py:79: UserWarning: WARN: Overwriting existing videos at /Users/josephbloom/GithubRepositories/DecisionTransformerInterpretability/videos/dt_eval_videos_0 folder (try specifying a different `video_folder` for the `RecordVideo` wrapper if this is not desired)
  logger.warn(
Evaluating DT: Episode 49 at timestep 15 for reward 0.856: 100%|██████████| 50/50 [00:06<00:00,  7.63it/s]              


In [52]:
statistics

# a calibration plot would measure mean_reward vs initial_rtg for rtg in some range 
# and then we can see if the model is over or under estimating the rtg.
import pandas as pd 
import plotly.express as px
import matplotlib.pyplot as plt
from tqdm import tqdm
import numpy as np

import warnings

def calibration_statistics(dt, env_id, make_env, initial_rtg_range = np.linspace(-1,1,21), trajectories=100):
    statistics = []
    pbar = tqdm(initial_rtg_range, desc="initial_rtg")
    for initial_rtg in pbar:
        statistics.append(evaluate_dt_agent(
            env_id = env_id,
            dt = dt,
            make_env=make_env,
            track = False,
            batch_number = 0,
            initial_rtg=initial_rtg,
            trajectories=trajectories,
            use_tqdm=False))
        pbar.set_description(f"initial_rtg: {initial_rtg}")
    return statistics

def plot_calibration_statistics(statistics):

    df = pd.DataFrame(statistics)

    fig = px.line(df, x="initial_rtg", y="mean_reward", title="Calibration Plot",
        template="plotly_white")
    fig.update_layout(
        xaxis_title="Initial RTG",
        yaxis_title="Mean Reward",
        legend_title="Proportion Completed",
    )
    fig.add_shape(
        type="line",
        x0=df.initial_rtg.min(), 
        y0=df.initial_rtg.min(),
        x1=df.initial_rtg.max(), 
        y1=df.initial_rtg.max(),
        line=dict(
            color="LightSeaGreen",
            width=4,
            dash="dashdot",
        )
    )

    # fig.show()
    return fig 

# suppress userwarnings
warnings.filterwarnings("ignore", category=UserWarning)
statistics = calibration_statistics(dt, env_id, make_env)
plot_calibration_statistics(statistics)

initial_rtg: 1.0: 100%|██████████| 21/21 [07:13<00:00, 20.63s/it]                 
/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [53]:
# let's load some trajectories 

# MiniGrid-Dynamic-Obstacles-8x8-v0__Dev__1__1673348123:v0
import wandb
run = wandb.init()
artifact = run.use_artifact('arena-ldn/DecisionTransformerInterpretability/MiniGrid-Dynamic-Obstacles-8x8-v0__Dev__1__1673348123:v0', type='model')
artifact_dir = artifact.download()


/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/notebook/utils.py:280: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/notebook/utils.py:280: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

wandb: Currently logged in as: jbloomaus (arena-ldn). Use `wandb login --relogin` to force relogin
/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/wandb/sdk/lib/ipython.py:46: DeprecationWarning:

Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display



/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/wandb/sdk/lib/ipython.py:46: DeprecationWarning:

Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display



/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/wandb/sdk/lib/ipython.py:46: DeprecationWarning:

Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display



wandb:   1 of 1 files downloaded.  


In [54]:

trajectory_path = "trajectories/MiniGrid-Dynamic-Obstacles-8x8-v0c8c5dccc-b418-492e-bdf8-2c21256cd9f3.pkl"
trajectory_data_set = TrajectoryLoader(trajectory_path, pct_traj=1, device="cpu")

env_id = trajectory_data_set.metadata['args']['env_id']
env = make_env(env_id, seed = 1, idx = 0, capture_video=False, run_name = "dev", fully_observed=False, max_steps=30)
env = env()

dt = DecisionTransformer(
    env = env, 
    d_model = 128,
    n_heads = 4,
    d_mlp = 256,
    n_layers = 2,
    state_embedding_type="grid", # hard-coded for now to minigrid.
    max_timestep=1000) # Our DT must have a context window large enough

path = "artifacts/MiniGrid-Dynamic-Obstacles-8x8-v0__Dev__1__1673348123:v0/MiniGrid-Dynamic-Obstacles-8x8-v0__Dev__1__1673348123.pt"
dt.load_state_dict(t.load(path))

# suppress userwarnings
warnings.filterwarnings("ignore", category=UserWarning)
# statistics = calibration_statistics(dt, env_id, make_env)
plot_calibration_statistics(statistics)

{'args': {'exp_name': 'MiniGrid-Dynamic-Obstacles-8x8-v0', 'seed': 1, 'cuda': True, 'track': True, 'wandb_project_name': 'PPO-MiniGrid', 'wandb_entity': None, 'capture_video': True, 'env_id': 'MiniGrid-Dynamic-Obstacles-8x8-v0', 'total_timesteps': 1800000, 'learning_rate': 0.00025, 'num_envs': 10, 'num_steps': 128, 'gamma': 0.99, 'gae_lambda': 0.95, 'num_minibatches': 10, 'update_epochs': 4, 'clip_coef': 0.4, 'ent_coef': 0.2, 'vf_coef': 0.5, 'max_grad_norm': 2, 'max_steps': 1000, 'trajectory_path': 'trajectories/MiniGrid-Dynamic-Obstacles-8x8-v0c8c5dccc-b418-492e-bdf8-2c21256cd9f3.pkl', 'fully_observed': False}, 'time': 1673347417.05341}


initial_rtg: 1.0: 100%|██████████| 21/21 [10:29<00:00, 29.96s/it]                  
/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [55]:
s, a, r, d, rtg, timesteps, mask = trajectory_data_set.get_batch(256,100)

In [62]:
timesteps[:10,-10:]

tensor([[ 30,  31,  32,  33,  34,  35,  36,  37,  38,  39],
        [  0,   0,  18,  19,  20,  21,  22,  23,  24,  25],
        [  1,   2,   3,   4,   5,   6,   7,   8,   9,  10],
        [ 43,  44,  45,  46,  47,  48,  49,  50,  51,  52],
        [210, 211, 212, 213, 214, 215, 216, 217, 218, 219],
        [597, 598, 599, 600, 601, 602, 603, 604, 605, 606],
        [421, 422, 423, 424, 425, 426, 427, 428, 429, 430],
        [ 37,  38,  39,  40,  41,  42,  43,  44,  45,  46],
        [ 32,  33,  34,  35,  36,  37,  38,  39,  40,  41],
        [  0,  24,  25,  26,  27,  28,  29,  30,  31,  32]])

In [67]:
px.histogram([i[-1] for i in trajectory_data_set.rewards if len(i) > 0])

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [72]:
# px.histogram([i.max() for i in trajectory_data_set.timesteps if len(i) > 0])

px.scatter(
    y=[i[-1] for i in trajectory_data_set.rewards if len(i) > 0],
    x=[i.max() for i in trajectory_data_set.timesteps if len(i) > 0],
    title="Reward vs Timesteps",
    template="plotly_white",
    labels={
        "x": "Timesteps",
        "y": "Reward",
    },
    marginal_x="histogram",
    marginal_y="histogram",
)

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [74]:
px.line(trajectory_data_set.get_sampling_probabilities())

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [78]:
sorted_inds = trajectory_data_set.get_indices_of_top_p_trajectories(trajectory_data_set.pct_traj)
px.scatter(
   x = trajectory_data_set.traj_lens[sorted_inds],
   y=  trajectory_data_set.get_sampling_probabilities()
)

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



# Let's do some analysis of the model

We want to be able to do 4 types of analysis:
1. looking at attention patterns and composition
2. backchaining the direction of maximum activation on a logit. This is like what we did in the brackets task.
3. Performing activation patching
4. Performing ablation

## Setup 

1. Get model and trajectories
2. 

In [3]:
# let's load our obstacle task model which does the funky wiggle at the end behavior
# https://wandb.ai/arena-ldn/DecisionTransformerInterpretability/runs/d5zjyan1/artifacts?workspace=user-jbloomaus
# import wandb
# run = wandb.init()
# artifact = run.use_artifact('arena-ldn/DecisionTransformerInterpretability/MiniGrid-Dynamic-Obstacles-8x8-v0__Dev__1__1673368088:v0', type='model')
# artifact_dir = artifact.download()
# run.finish()

# the trajectory path: "trajectories/MiniGrid-Dynamic-Obstacles-8x8-v0c8c5dccc-b418-492e-bdf8-2c21256cd9f3.pkl"
model_path = "artifacts/MiniGrid-Dynamic-Obstacles-8x8-v0__Dev__1__1673368088:v0/MiniGrid-Dynamic-Obstacles-8x8-v0__Dev__1__1673368088.pt"

In [1]:
# first, we need a trajectory loader and a model. 
import torch as t 
from src.decision_transformer.offline_dataset import TrajectoryLoader
from src.decision_transformer.model import DecisionTransformer
from src.environments import make_env

trajectory_path = "trajectories/MiniGrid-Dynamic-Obstacles-8x8-v0c8c5dccc-b418-492e-bdf8-2c21256cd9f3.pkl"
trajectory_data_set = TrajectoryLoader(trajectory_path, pct_traj=1, device="cpu")

env_id = trajectory_data_set.metadata['args']['env_id']
env = make_env(env_id, seed = 1, idx = 0, capture_video=False, run_name = "dev", fully_observed=False, max_steps=30)
env = env()

dt = DecisionTransformer(
    env = env, 
    d_model = 128,
    n_heads = 4,
    d_mlp = 256,
    n_layers = 2,
    n_ctx=3000,
    layer_norm=False,
    state_embedding_type="grid", # hard-coded for now to minigrid.
    max_timestep=1000) # Our DT must have a context window large enough

model_path = "artifacts/MiniGrid-Dynamic-Obstacles-8x8-v0__Dev__1__1673368088:v0/MiniGrid-Dynamic-Obstacles-8x8-v0__Dev__1__1673368088.pt"
dt.load_state_dict(t.load(model_path))

{'args': {'exp_name': 'MiniGrid-Dynamic-Obstacles-8x8-v0', 'seed': 1, 'cuda': True, 'track': True, 'wandb_project_name': 'PPO-MiniGrid', 'wandb_entity': None, 'capture_video': True, 'env_id': 'MiniGrid-Dynamic-Obstacles-8x8-v0', 'total_timesteps': 1800000, 'learning_rate': 0.00025, 'num_envs': 10, 'num_steps': 128, 'gamma': 0.99, 'gae_lambda': 0.95, 'num_minibatches': 10, 'update_epochs': 4, 'clip_coef': 0.4, 'ent_coef': 0.2, 'vf_coef': 0.5, 'max_grad_norm': 2, 'max_steps': 1000, 'trajectory_path': 'trajectories/MiniGrid-Dynamic-Obstacles-8x8-v0c8c5dccc-b418-492e-bdf8-2c21256cd9f3.pkl', 'fully_observed': False}, 'time': 1673347417.05341}


<All keys matched successfully>

In [2]:
s, a, r, d, rtg, timesteps, mask = trajectory_data_set.get_batch(256,100)

In [3]:
from src.visualization import render_minigrid_observations
import plotly.express as px 
px.imshow(
    render_minigrid_observations(env, s[0][mask[0].to(bool)]),
    animation_frame=0).show()
px.line(
    x=timesteps[0][mask[0].to(bool)],
    y=rtg[0,1:][mask[0].to(bool)].flatten(),
)

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/plotly/io/_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [4]:
rtg[0].shape

torch.Size([101, 1])

In [5]:
rtg[0,1:][mask[0].to(bool)].shape

torch.Size([32, 1])

In [24]:
import numpy as np
import torch


def evaluate_episode(
        env,
        state_dim,
        act_dim,
        model,
        max_ep_len=1000,
        device='cuda',
        target_return=None,
        mode='normal',
        state_mean=0.,
        state_std=1.,
):

    model.eval()
    model.to(device=device)

    # state_mean = torch.from_numpy(state_mean).to(device=device)
    # state_std = torch.from_numpy(state_std).to(device=device)

    state, _ = env.reset()

    # we keep all the histories on the device
    # note that the latest action and reward will be "padding"
    states = torch.from_numpy(state['image']).reshape(1, *state_dim).to(device=device, dtype=torch.float32)
    
    actions = torch.zeros((0, act_dim), device=device, dtype=torch.float32)
    rewards = torch.zeros(0, device=device, dtype=torch.float32)
    target_return = torch.tensor(target_return, device=device, dtype=torch.float32)
    sim_states = []

    episode_return, episode_length = 0, 0
    for t in range(max_ep_len):

        # add padding
        actions = torch.cat([actions, torch.zeros((1, act_dim), device=device)], dim=0)
        rewards = torch.cat([rewards, torch.zeros(1, device=device)])

        action = model.get_action(
            states = states.to(dtype=torch.float32).unsqueeze(0),
            actions = actions.to(dtype=torch.long).unsqueeze(0),
            rtgs = target_return - rewards.to(dtype=torch.float32).unsqueeze(0).unsqueeze(0),
            timesteps = torch.tensor(t, device=device, dtype=torch.long).reshape(1, 1).unsqueeze(0),
        )
        actions[-1] = action
        action = action.detach().cpu().numpy()

        state, reward, done, trunc, info = env.step(action)

        cur_state = torch.from_numpy(state).to(device=device).reshape(1, state_dim)
        states = torch.cat([states, cur_state], dim=0)
        rewards[-1] = reward

        episode_return += reward
        episode_length += 1

        if done:
            break

    return episode_return, episode_length


evaluate_episode(
    env, 
    env.observation_space['image'].shape, 
    env.action_space.n, 
    dt, 
    max_ep_len=1000, 
    device='cpu', 
    target_return=1, 
    mode='normal', 
    state_mean=np.array([0]), 
    state_std=np.array([1])
)

EinopsError:  Error while processing rearrange-reduction pattern "batch block action -> (batch block) action".
 Input tensor shape: torch.Size([1, 1]). Additional info: {}.
 Expected 3 dimensions, got 2

In [25]:
import wandb
run = wandb.init()
artifact = run.use_artifact('arena-ldn/DecisionTransformerInterpretability/MiniGrid-Dynamic-Obstacles-8x8-v0__MiniGrid-Dynamic-Obstacles-8x8-v0__1__1673546242:v0', type='model')
artifact_dir = artifact.download()

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/notebook/utils.py:280: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/notebook/utils.py:280: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

wandb: Currently logged in as: jbloomaus (arena-ldn). Use `wandb login --relogin` to force relogin
/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/wandb/sdk/lib/ipython.py:46: DeprecationWarning:

Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display



/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/wandb/sdk/lib/ipython.py:46: DeprecationWarning:

Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display



/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/wandb/sdk/lib/ipython.py:46: DeprecationWarning:

Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display



/Users/josephbloom/miniforge3/envs/decision_transformer_interpretability/lib/python3.9/site-packages/wandb/sdk/lib/ipython.py:46: DeprecationWarning:

Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display



wandb:   1 of 1 files downloaded.  
